In [7]:
import os
import urllib.request, json 
import pandas as pd
from IPython.display import HTML
from IPython import display
from pyciemss.PetriNetODE.interfaces import (
    load_and_sample_petri_model,
    load_and_calibrate_and_sample_petri_model,
    load_petri_model,
    setup_petri_model,
    sample
)
import numpy as np
from typing import Iterable
from pyciemss.utils.interface_utils import (
    assign_interventions_to_timepoints,
    interventions_and_sampled_params_to_interval,
    convert_to_output_format
)
from pyciemss.utils import get_tspan
from pyciemss.visuals import plots
import matplotlib.pyplot as plt
import torch
from torch import tensor

In [8]:
COLORS=['red','green','blue','black','gold','purple','orangered']

def aggregate_results(samples_df, num_samples=1):
    QoIs = ["D_sol", "E_sol", "I_sol", "R_sol", "S_sol"]
    all_QoIs = {key: None for key in QoIs}
    for QoI in QoIs:
        # Aggregate results
        # TODO: After they introduce normalized models, remove normalization here.
        # /total_pop * 100
        # total_pop = 0
        # for val in QoIs:
        #     total_pop += samples_df[samples_df["sample_id"] == 0][val].to_numpy()[0]
        all_QoIs[QoI] = [samples_df[samples_df["sample_id"] == i][QoI].to_numpy() for i in range(num_samples)]
    return all_QoIs

def plotseird(t, S=None, E=None, I=None, R=None, D=None, L=None, R0=None, Alpha=None, CFR=None, ax=None):
    if ax is None:
        f, ax = plt.subplots(1,1,figsize=(10,4))
    N = S[0] + E[0] + I[0] + R[0] + D[0]
    if S is not None:
        ax.plot(t, (S/N)*100, 'b--', alpha=0.7, linewidth=2, label='Susceptible')
    if E is not None:
        ax.plot(t, (E/N)*100, 'y.', alpha=0.7, linewidth=2, label='Exposed')
    if I is not None:
        ax.plot(t, (I/N)*100, 'r', alpha=0.7, linewidth=2, label='Infected')
    if R is not None:
        ax.plot(t, (R/N)*100, 'g-.', alpha=0.7, linewidth=2, label='Recovered')

    if D is not None:
        ax.plot(t, D/N, 'k', alpha=0.7, linewidth=2, label='Dead')
        ax.plot(t, ((S+E+I+R+D)/N)*100, 'c:', alpha=0.7, linewidth=2, label='Total')
    else:
        ax.plot(t, ((S+E+I+R)/N)*100, 'c:', alpha=0.7, linewidth=2, label='Total')

    ax.set_xlabel('Time (days)')
    ax.set_ylabel('Percentage of Population (%)')

    ax.yaxis.set_tick_params(length=0)
    ax.xaxis.set_tick_params(length=0)
    ax.grid(visible=True, which='major', c='w', lw=2, ls='-')
    legend = ax.legend(borderpad=2.0)
    legend.get_frame().set_alpha(0.5)
    for spine in ('top', 'right', 'bottom', 'left'):
        ax.spines[spine].set_visible(False)
    if L is not None:
        plt.title("Lockdown after {} days".format(L))
    # plt.show()

    if R0 is not None or CFR is not None:
        f = plt.figure(figsize=(12,4))
    
    if R0 is not None:
        # sp1
        ax1 = f.add_subplot(121)
        ax1.plot(t, R0, 'b--', alpha=0.7, linewidth=2, label='R_0')

        ax1.set_xlabel('Time (days)')
        ax1.title.set_text('R_0 over time')
        # ax.set_ylabel('Number (1000s)')
        # ax.set_ylim(0,1.2)
        ax1.yaxis.set_tick_params(length=0)
        ax1.xaxis.set_tick_params(length=0)
        ax1.grid(b=True, which='major', c='w', lw=2, ls='-')
        legend = ax1.legend()
        legend.get_frame().set_alpha(0.5)
        for spine in ('top', 'right', 'bottom', 'left'):
            ax.spines[spine].set_visible(False)

    if Alpha is not None:
        # sp2
        ax2 = f.add_subplot(122)
        ax2.plot(t, Alpha, 'r--', alpha=0.7, linewidth=2, label='alpha')

        ax2.set_xlabel('Time (days)')
        ax2.title.set_text('fatality rate over time')
        # ax.set_ylabel('Number (1000s)')
        # ax.set_ylim(0,1.2)
        ax2.yaxis.set_tick_params(length=0)
        ax2.xaxis.set_tick_params(length=0)
        ax2.grid(b=True, which='major', c='w', lw=2, ls='-')
        legend = ax2.legend()
        legend.get_frame().set_alpha(0.5)
        for spine in ('top', 'right', 'bottom', 'left'):
            ax.spines[spine].set_visible(False)

    # plt.show()

In [9]:
# Add '?raw=true' at the end of the link to the file to get the rawgithubusercontent link.

def update_AMR(SEIRD_model_url, SEIRD_model_path):
    with urllib.request.urlopen(SEIRD_model_url) as url:
        json_object = json.load(url)
        with open(SEIRD_model_path, "w") as outfile:
            json.dump(json_object, outfile)

def change_model_parameters(filename, new_params):
    # new params = [(param, value), (param, value)]
    with open(filename, 'r') as f:
        model = json.load(f)
        # Change initial parameters
        for (param, value) in new_params:
            for idx in model["semantics"]["ode"]["parameters"]:
                if idx["id"] == param:
                    idx["value"] = value
    return model

In [10]:
num_samples = 1
start_time = 0
end_time = 31 # Next 4 weeks of the pandemic.
num_timepoints = (end_time-start_time)*10 + 1
timepoints = list(get_tspan(start_time, end_time, num_timepoints).detach().numpy())

In [11]:
SEIRD_model_path = "scenario1_a_ii_1.json"
SEIRD_model_url = "https://raw.githubusercontent.com/indralab/mira/hackathon/notebooks/evaluation_2023.07/eval_scenario1_1_ii_1.json"
# NOTE: This is only if you wish to update the AMR.
update_AMR(SEIRD_model_url, SEIRD_model_path)

# model = change_model_parameters(SEIRD_model_path, [("t_0", 0)])
# "subset":".*_sol"
results_1_a_ii_1 = load_and_sample_petri_model(
        SEIRD_model_path, num_samples, timepoints=timepoints, visual_options={"title": "1(a)(ii)(1)", "subset":["D_sol", "I_sol", "R_sol", "E_sol"]}, time_unit="days")
plots.ipy_display(results_1_a_ii_1["visual"])
# QoIs_0day = aggregate_results(samples_1_a_ii_1, num_samples)

In [12]:
SEIRD_model_path = "scenario1_a_ii_2.json"
SEIRD_model_url = "https://raw.githubusercontent.com/indralab/mira/hackathon/notebooks/evaluation_2023.07/eval_scenario1_1_ii_2.json"
# NOTE: This is only if you wish to update the AMR.
update_AMR(SEIRD_model_url, SEIRD_model_path)

results_1_a_ii_2 = load_and_sample_petri_model(
        SEIRD_model_path, num_samples, timepoints=timepoints, visual_options={"title": "1(a)(ii)(2)", "subset":["D_sol", "I_sol", "R_sol", "E_sol"]}, time_unit="days")
plots.ipy_display(results_1_a_ii_2["visual"])

In [17]:
# Add distributions to some of the parameters.
def add_distribution(filename, new_params):
    """
              "distribution": {
            "type": "Uniform1",
            "parameters": {
              "minimum": 0.026,
              "maximum": 0.028
            }
          }
    """
    # new params = [(param, new_distribution), (param, new_distribution)]
    with open(filename, 'r') as f:
        model = json.load(f)
        # Change initial parameters
        for (param, new_distribution) in new_params:
            for idx in model["semantics"]["ode"]["parameters"]:
                if idx["id"] == param:
                    idx["distribution"] = new_distribution
    return model

model = add_distribution(SEIRD_model_path, [("beta_c", {"type": "Uniform1", "parameters": {"minimum": 0.0001, "maximum": 0.9999}})])
results_1_a_ii_2_distr = load_and_sample_petri_model(
        model, num_samples=100, timepoints=timepoints, visual_options={"title": "1(a)(ii)(2)", "subset":["D_sol", "I_sol", "R_sol", "E_sol"]}, time_unit="days")
plots.ipy_display(results_1_a_ii_2_distr["visual"])

In [52]:
SEIRD_model_path = "scenario1_a_ii_3.json"
SEIRD_model_url = "https://raw.githubusercontent.com/indralab/mira/hackathon/notebooks/evaluation_2023.07/eval_scenario1_1_ii_3.json"
# NOTE: This is only if you wish to update the AMR.
update_AMR(SEIRD_model_url, SEIRD_model_path)
QoIs = ["I_compliant_sol", "I_noncompliant_sol", "R_sol", "E_compliant_sol", "E_noncompliant_sol", "H_sol"]
results_1_a_ii_3 = load_and_sample_petri_model(
        SEIRD_model_path, num_samples, timepoints=timepoints, visual_options={"title": "1(a)(ii)(3)", "subset":QoIs}, time_unit="days")
plots.ipy_display(results_1_a_ii_3["visual"])

In [58]:
SEIRD_model_path = "scenario1_2_sirhd.json"
SEIRD_model_url = "https://raw.githubusercontent.com/indralab/mira/hackathon/notebooks/evaluation_2023.07/eval_scenario1_2_sirhd.json"
# NOTE: This is only if you wish to update the AMR.
update_AMR(SEIRD_model_url, SEIRD_model_path)
QoIs = ["I_sol", "R_sol", "E_sol", "H_sol", "D_sol"]
results_1_2_ab_1 = load_and_sample_petri_model(
        SEIRD_model_path, num_samples, timepoints=timepoints, visual_options={"title": "1(2)(ab)(1)", "subset":QoIs}, time_unit="days")
plots.ipy_display(results_1_2_ab_1["visual"])

In [69]:
# find all keys that end with _sol
solution_headers = [key for key in results_1_2_ab_2["data"].keys() if key.endswith("_sol")]
# find all keys in solution_headers that don't start with S
solution_headers = [key for key in solution_headers if not key.startswith("S")]
print(solution_headers)

['D_0_4_sol', 'D_10_14_sol', 'D_15_19_sol', 'D_20_24_sol', 'D_25_29_sol', 'D_30_34_sol', 'D_35_39_sol', 'D_40_44_sol', 'D_45_49_sol', 'D_50_54_sol', 'D_55_59_sol', 'D_5_9_sol', 'D_60_64_sol', 'D_65_69_sol', 'D_70_74_sol', 'D_75_79_sol', 'D_80_84_sol', 'D_85_sol', 'H_0_4_sol', 'H_10_14_sol', 'H_15_19_sol', 'H_20_24_sol', 'H_25_29_sol', 'H_30_34_sol', 'H_35_39_sol', 'H_40_44_sol', 'H_45_49_sol', 'H_50_54_sol', 'H_55_59_sol', 'H_5_9_sol', 'H_60_64_sol', 'H_65_69_sol', 'H_70_74_sol', 'H_75_79_sol', 'H_80_84_sol', 'H_85_sol', 'I_0_4_sol', 'I_10_14_sol', 'I_15_19_sol', 'I_20_24_sol', 'I_25_29_sol', 'I_30_34_sol', 'I_35_39_sol', 'I_40_44_sol', 'I_45_49_sol', 'I_50_54_sol', 'I_55_59_sol', 'I_5_9_sol', 'I_60_64_sol', 'I_65_69_sol', 'I_70_74_sol', 'I_75_79_sol', 'I_80_84_sol', 'I_85_sol', 'R_0_4_sol', 'R_10_14_sol', 'R_15_19_sol', 'R_20_24_sol', 'R_25_29_sol', 'R_30_34_sol', 'R_35_39_sol', 'R_40_44_sol', 'R_45_49_sol', 'R_50_54_sol', 'R_55_59_sol', 'R_5_9_sol', 'R_60_64_sol', 'R_65_69_sol', 'R_7

In [70]:
SEIRD_model_path = "scenario1_2_sirhd_age.json"
SEIRD_model_url = "https://raw.githubusercontent.com/indralab/mira/hackathon/notebooks/evaluation_2023.07/eval_scenario1_2_sirhd_age.json"
# NOTE: This is only if you wish to update the AMR.
update_AMR(SEIRD_model_url, SEIRD_model_path)
QoIs = ["I_sol", "R_sol", "E_sol", "H_sol", "D_sol"]
results_1_2_ab_2 = load_and_sample_petri_model(
        SEIRD_model_path, num_samples, timepoints=timepoints, visual_options={"title": "1(2)(ab)(2)", "subset":solution_headers}, time_unit="days")
plots.ipy_display(results_1_2_ab_2["visual"])